# mm2nested_lists

Dieses Notebook: Eine kleine Utility, die eine Freeplane-Mindmap in eine *nested list* überführt, und als JSON-Datei 'rausschreibt.


Idee:
* Kindknoten eines Knotens werden repräsentiert durch eine Liste von Knoten.

## Beispiel

* Input: die Mindmap {download}`test.mm`
* Output: die JSON-Datei {download}`test.mm.json`

Aufbau der Mindmap: Die Mindmap `test.mm` hat die Root-Node mit dem Text `test` und die Kindknoten (mit dem Text) `a`, `b` und `c`. Knoten `b` hat selbst wieder die Kindknoten `ba` und `bb`:

* test
  * a
  * b
    * ba
    * bb
  * c


Die Ergebnis-Liste soll so aussehen:

```
['test', [ 'a', 'b', ['ba', 'bb'] ], 'c']
```

In [1]:
mm_path = "./test.mm"

In [2]:
# wir verwenden die xml und xslt-Engine
# https://lxml.de/
from lxml import etree

# https://pypi.org/project/markdownify/
# pip install markdownify
from markdownify import markdownify

In [3]:
mm_path = "./test.mm"

# https://lxml.de/
from lxml import etree
parser = etree.XMLParser(remove_blank_text=True)
etree_tree = etree.parse(mm_path, parser)
etree_startnode = etree_tree.getroot().find("node")

In [4]:
def representation(n):
    """returns a text represenatation of a .mm XML element"""
    
    if n.tag == "node":
        if n.find('richcontent[@TYPE="NODE"]') is not None:
            # wir haben einen richconten Knoten:
            # html Knoteninhalt als Markdown zurückliefern
            return markdownify(
                etree.tostring(n.find('richcontent[@TYPE="NODE"]'), 
                    encoding="utf8"), heading_style="ATX")
        else:
            # wir haben einen einfachen Knoten:
            # Knoteninhalt steht im Attribut "TEXT"
            return n.get("TEXT")
    else:
        return n.tag
    
def walk(current, result):
    """Returns a nested dict representation of a freeplane mindmap."""    
    
    # current ist immer eine XML-Node mit dem Namen node
    result.append( representation( current ) )
    
    
    # Liste aller "node"-Kinder des aktuellen Knotens
    # (andere XML-Elemente sind uninteressant)
    children = current.findall("node")
    
    if len(children) >= 1:
        # der aktuelle Knoten *hat* Kinder:
        # Wir geben eine Liste zurück, deren erstes Element der aktuelle Knoten selbst ist:
        
        # print([ c.get("TEXT") for c in children ])
        sub_list = []
        
        for child in children:
            walk(child, sub_list)
        result.append( sub_list )


In [5]:
etree_startnode.tag

'node'

In [6]:
ergebnis = []
walk( etree_startnode, ergebnis )
ergebnis


['test',
 ['a',
  'b',
  ['ba',
   'bb',
   '',
   '\n# \n Hallo Welt!\n\n\n\n\n\n Das ist eine **richcontent**\xa0Node\n \n\n'],
  'c']]

## JSON

Wir schreiben das Ergebnis als JSON-Datei 'raus:

In [7]:
import json
mm_json_object = json.dumps(ergebnis, indent=2)
with open(mm_path+'.json', 'w') as outfile:
    outfile.write(mm_json_object)

Ergebnis:  Im gleichen Verzeichnis wie unsere Mindmap {download}`./test.mm` liegt jetzt die JSON-Datei {download}`test.mm.json`.